# 800100715151 Astronomide Veritabanları #
## Ders - 05c Astronomi Verisi İçin Özelleştirilmiş Bir Sorgulama Dili: ##
## Astronomical Data Query Language (ADQL) ##

# Bu derste neler öğreneceksiniz? #
## Astronomi Verisi için Özelleştirilmiş Bir Sorgulama Dili ADQL ##

* [Astronomical Data Query Language: ADQL](#Astronomical-Data-Query-Language:-ADQL)
    * [Matematiksel Fonksiyon ve Operatörler](#Matematiksel-Fonksiyon-ve-Operatörler)
    * [Geometrik Fonksiyon ve Operatörler](#Geometrik-Fonksiyon-ve-Operatörler)
    * [Alt sorgular (Subqueries)](#Alt-sorgular-(Subqueries))
    * [Sorgu Birleştirme İşlemleri](#Sorgu-Birleştirme-İşlemleri)
    * [Koşullu Sorgular](#Koşullu-Sorgular)
* [ADQL Örnekleri](#ADQL-Örnekleri)
    * [Simbad Veritabanı ADQL Örnekleri](#Simbad-Veritabanı-ADQL-Örnekleri)
    * [Gaia Veritabanı ADQL Örnekleri](#Gaia-Veritabanı-ADQL-Örnekleri)
* [Kaynaklar](#Kaynaklar)

## Astronomical Data Query Language: ADQL ##

[Astronomical Data Query Language (ADQL)](https://www.ivoa.net/documents/ADQL/20180112/PR-ADQL-2.1-20180112.html), Uluslararası Sanal Gözlemevleri Birliği (IVOA) tarafından sanal gözlemevi (VO) servislerine gönderilen astronomiye özgü sorguları için kullanılan, yapısal sorgulama dilinin (SQL) özelleştirilmiş bir versiyonudur. IVOA, astronomi verilerine erişmek için çeşitli standartlaştırılmış protokoller geliştirmiştir. Örnek olarak görüntü ve tayfsal verilere erişim için için kullanılan Basit Görüntü Erişimi (Simple Image Access, SIA) ve Basit Tayfsal Veri Erişimi (Simple Spectral Access, SSA) protokolleri verilebilir. Bu protokoller aracılığıyla veri sorgulamak ve farklı VO servislerinin sorgu karmaşıklığına, astronomiye özgü bazı fonksiyonları da kullanarak kolaylık getirmek amacıyla geliştirilmiştir.

ADQL, bazı astronomi verisini sorgularken çok kullanılan bazı fonksiyonları içermektedir. Bunlar;

### Matematiksel Fonksiyon ve Operatörler ###
ABS, ACOS, ASIN, ATAN, ATAN2, CEILING, COS, DEGREES, EXP, FLOOR, LOG, LOG10, MOD, PI, POWER, RADIANS, RAND, ROUND, SIN, SQRT, TAN, TOP, TRUNCATE

### Geometrik Fonksiyon ve Operatörler ###
AREA, BOX, CENTROID, CIRCLE, CONTAINS, COORD1, COORD2, COORDSYS, DISTANCE, INTERSECTS, POINT, POLYGON, REGION

Bir ADQL sorgusunun temel yapısı;

```
SELECT
        [ ALL | DISTINCT ]
        [ TOP unsigned_decimal ]
        {
             * |
             { value_expression [ [AS] column_name ] }, ...
         }
        FROM {
                {
                table_name [ [AS] identifier ] |
                ( SELECT ....) [ [AS] identifier ] |
                table_name [NATURAL]
                    [ INNER | { LEFT | RIGHT | FULL [OUTER] } ]
                    JOIN table_name
                    [ON search_condition | USING ( column_name,...) ]
                },
            ...
            }

        [ WHERE search_condition ]
        [ GROUP BY group_by_term, ... ]
        [ HAVING search_condition ]
        [ ORDER BY
            { order_by_expression } [ ASC | DESC],
            ...
            ]
        [ OFFSET unsigned_decimal ]
```
şeklindedir.

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

### Alt sorgular (Subqueries) ###
Tablo alt sorguları, bir sorgunun `WHERE` ile verilen bir koşul için `IN` ve `EXISTS` gibi yapılar ile birleştirilmesiyle kurgulanabilir.

```
SELECT
        alpha_source.id
    FROM 
        alpha_source
    WHERE
        alpha_sourceid >=5
    AND
        alpha_sourceid IN 
            (
            SELECT id FROM alpha_source WHERE id < 10
            )
```

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

### Sorgu Birleştirme İşlemleri ###

ADQL, `INNER` ve `OUTER` (`LEFT`, `RIGHT` ve `FULL`) birleştirmelerini destekler. Herhangi bir tür belirtilmezse varsayılan değer `INNER` olur. 

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

### Koşullu Sorgular ###

SQL dilinin yapıları olan `JOIN`, `HAVING` ve `WHERE` ifadeleri kullanılarak sorgular koşullara bağlanabilir. Bu amaçla karşılaştırma operatörleri ("=, !=, <>, <, >, <=, >=") gibi yapılardan, `NOT`,`BETWEEN`, `LIKE`, `ILIKE` gibi ifadelerden, `IS NULL`, `IS NOT NULL` ve `EXISTS` gibi kontrol yapılarından faydalanılabilir.

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

# ADQL Örnekleri #

ADQL kullanımıı örneklendirmek üzere aşağıda Simbad ve Gaia veritabanlarını sorgulamak üzere seçilmiş bazı örnekler yer almaktadır. Bu örnekler için ilgili veritabanlarına `astroquery` modülü fonksiyonları aracılığıyla bağlanılacaktır.

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

## Simbad Veritabanı ADQL Örnekleri ##

Simbad veritabanında ADQL sorguları [Table Access Protocol (TAP)](https://simbad.cds.unistra.fr/simbad/sim-tap/) servisi aracılığyla gerçekleştirilir. `astroquery.simbad` modülü bu servise string formatında kurgulanan sorguları `query_tap` fonksiyonu ile gönderir. Dönen sonuç bir `astropy` tablosudur.

In [ ]:
import astroquery
from astroquery.gaia import Gaia
from astroquery.simbad import Simbad

In [ ]:
Simbad.ROW_LIMIT = -1

#### Örnek-1: İsimlerinden biri sağlanan bir nesnenin temel parametrelerinin çekilmesi

Aşağıdaki sorguda <b><i>M13</i></b>'ün `OID`, `RA`, `DEC`, `main_id` gibi bazı temel parametrelerinin yanısıra `galdim_majaxix`, `galdim_minaxis`, `galdim_angle` gibi galaksinin şeklini tanımalayan parametreleri Simbad veritabanının [<i>"Basic Search"</i>](http://simbad.cds.unistra.fr/simbad/sim-fbasic) ile erişilen $basic$ ile [<i>"By Identifier Search"</i>](http://simbad.cds.unistra.fr/simbad/sim-fid) ile erişilen $ident$ tabloları sırasıyla `OID` ve `OIDREF` sütunları üzerinden bağlanarak  sorgulanmasıyla elde edilmektedir.

In [ ]:
# Basic data from an object given one of its identifiers.
adql_simbad_sorgu1 = """SELECT basic.OID,
       RA,
       DEC,
       main_id AS "Main identifier",
       coo_bibcode AS "Coord Reference",
       nbref AS "Number of References",
       plx_value as "Parallax",
       rvz_radvel as "Radial velocity",
       galdim_majaxis,
       galdim_minaxis,
       galdim_angle AS "Galaxy ellipse angle"
FROM basic JOIN ident ON oidref = oid
WHERE id = 'm13';"""
r = Simbad.query_tap(adql_simbad_sorgu1)
print(r['Main identifier','galdim_majaxis','galdim_minaxis','Galaxy ellipse angle'])

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

#### Örnek-2: Bibliyografik referansı (künyesi) verilen bir yayında yer alan nesnelerin çekilmesi ####

Aşağıdaki sorguda $2006AJ.131.1163S$ referansında yer alan nesneler [<i>"Reference Query"</i>](http://simbad.cds.unistra.fr/simbad/sim-fref) yoluyla erişilen $has\_ref$ ve [<i>"Basic Query"</i>](http://simbad.cds.unistra.fr/simbad/sim-fbasic) yoluyla erişilen $basic$ tablolarının sırasıyla `oidref` ve `oid` sütunları üzerinden bağlanmasıyla elde edilen ve `basic.OID` ve `main_id` sütunlarından oluşan tablo, `main_id` (sorgudaki lakabı `Identifier` olarak belirlenmektedir) sütununa göre sıralanmaktadır.

In [ ]:
# Display objects contained in a given bibliographic reference.
adql_simbad_sorgu2 = """SELECT basic.OID, main_id AS "Identifier"
FROM has_ref JOIN basic ON oidref = oid JOIN ref ON oidbibref = oidbib
WHERE bibcode = '2006AJ.131.1163S'
ORDER BY "Identifier";"""
r = Simbad.query_tap(adql_simbad_sorgu2)
r

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

#### Örnek-3: Bir nesnenin çeşitli fotometrik bantlardaki parlaklıklarının çekilmesi ####

Aşağıdaki ADQL sorgusunda Simbad veritabanının $allfluxes$ tablosundan `B`,`V`,`R`,`I`,`J` sütunları, bu tablonun [<i>"Identifier Query"</i>](http://simbad.cds.unistra.fr/simbad/sim-fid) ile erişilen $ident$ tablosunun `oidref` sütunları üzerinden bağlanmasıyla <i>M13</i> cismi için elde edilmektedir.

In [ ]:
# Basic magnitudes of an object (from one identifier)
adql_simbad_sorgu3 = """SELECT B, V, R ,I , J from allfluxes
JOIN ident USING(oidref)
WHERE id = 'm13';"""
r = Simbad.query_tap(adql_simbad_sorgu3)
r

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

## Gaia Veritabanı ADQL Örnekleri ##

Gaia veritabanında ADQL sorguları [Gaia Veri Arşivi](https://gea.esac.esa.int/archive/) "Advanced ADQL" servisi aracılığyla gerçekleştirilir. `astroquery.gaia` modülü bu servise string formatında kurgulanan sorguları `launch_job` fonksiyonu ile gönderir. Sorgu nesnesinin `get_results()` metodu, istenen sorgu sonucunu, bir `astropy` tablosu olarak verir.

#### Örnek-1: Belirli bir dairesel alandan seçilen noktaların bir gökyüzü koordinatına açısal uzaklıkları

Aşağıdaki sorguda koordinatları $RA = 81^{\circ}.28$ ve $DEC = -69^{\circ}.78$ olan bir noktaya, bu sağaçıklık ve dikaçıklık merkezli, 5 yaydakikası yarıçapında bir çemberin içinde kalan `gaiadr3.gaia_source` Gaia DR3 cisimlerinden 20.5 kadirden daha parlak ve paralaks değeri ölçülmüş olanlarının tüm sütunları ve bu noktaya olan açısal uzaklıklıklarından oluşan bir tablo elde edilmektedir.

In [ ]:
# Cone search sorted by angular separation
adql_gaia_sorgu1 = """SELECT *, DISTANCE(POINT(81.28, -69.78), POINT(ra, dec)) AS ang_sep
FROM gaiadr3.gaia_source WHERE 1 = CONTAINS(
POINT(81.28, -69.78),CIRCLE(ra, dec, 5./60.))
AND phot_g_mean_mag < 20.5
AND parallax IS NOT NULL
ORDER BY ang_sep ASC"""
job = Gaia.launch_job(adql_gaia_sorgu1)
r = job.get_results()
#r['DESIGNATION','ra','dec','ang_sep'].pprint_all()

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

#### Örnek-2: HIPPARCOS ve Gaia Veritabanlarının Çapraz Eşleştirmesi ####

Aşağıdaki sorguda `public.hipparcos` tablosunun `gaiadr3.gaia_source` tablosuyla $0^{\circ}.00028$'lik bir tolerans değeri ile çapraz eşleştirilmesi sonrası biribiriyle eşleşen ilk 1000 satırın tüm sütunları ve her iki katalogdaki konumları arası açısal uzaklık ($ang\_sep$) değerlerinden oluşan bir tablo elde edilmektedir.

In [ ]:
# Basic positional cross-match between HIPPARCOS & Gaia
adql_gaia_sorgu2 = """SELECT TOP 1000 *, DISTANCE(POINT(hip.ra, hip.de),
POINT(gaia.ra, gaia.dec)) AS ang_sep
FROM public.hipparcos AS hip
JOIN gaiadr3.gaia_source AS gaia 
ON 1 = CONTAINS(
   POINT(hip.ra, hip.de),
   CIRCLE(gaia.ra, gaia.dec, 0.00028))"""
job = Gaia.launch_job(adql_gaia_sorgu2)
r = job.get_results()
#r['DESIGNATION','hip','ang_sep'].pprint_all()

#### Örnek-3: Gaia DR2 ve EDR3'nin Çapraz Eşleştirmesi

Aşağıdaki sorguda Gaia Data-Release 2 (DR2) ($gaiadr2.gaia\_source$) ve Early Data Release-3 (EDR3) ($gaiadr3.dr2\_neighbourhood$) tablolarının sırasıyla `dr2.source_id` ve `dr3.dr2_source_id` sütunları üzerinden bağlanması sonucu $G$ bandında ortalama olarak 5 kadirden parlak cisimlerin her iki katalogdaki ID numaraları ve parlaklıklarının artan sırada sıralandığı bir tablo oluşmaktadır.

In [ ]:
# Bright sources in DR2 and EDR3
adql_gaia_sorgu3 = """SELECT dr2.source_id, dr2.phot_g_mean_mag, dr3.*
FROM gaiadr2.gaia_source AS dr2
JOIN gaiadr3.dr2_neighbourhood AS dr3 ON dr2.source_id = dr3.dr2_source_id
WHERE dr2.phot_g_mean_mag < 5
ORDER BY dr2.source_id ASC"""
job = Gaia.launch_job(adql_gaia_sorgu3)
r = job.get_results()
r['source_id','dr2_source_id','phot_g_mean_mag']

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)

# Kaynaklar

1. [Astronomical Data Query Language](https://www.ivoa.net/documents/ADQL/20180112/PR-ADQL-2.1-20180112.html#sec:features)
2. [Simbad Table Access Protocol (TAP) Servisi](http://simbad.cds.unistra.fr/simbad/sim-tap/)
3. [ESA Gaia Veri Arşivi](http://simbad.cds.unistra.fr/simbad/sim-tap/)
4. [astroquery Dokümantasyonu](https://astroquery.readthedocs.io/en/latest/)

[Başa Dön](#Bu-derste-neler-öğreneceksiniz?)